# Biblioteca de Algoritmos - Lab 03

Nos últimos anos, muitas bibliotecas RL foram desenvolvidas. Essas bibliotecas foram projetadas para ter todas as ferramentas necessárias para implementar e testar agentes de Aprendizado por Reforço .

Ainda assim, elas se diferem muito. É por isso que é importante escolher uma biblioteca que seja rápida, confiável e relevante para sua tarefa de RL. Do ponto de vista técnico, existem algumas coisas a se ter em mente ao considerar uma bilioteca para RL.

- **Suporte para bibliotecas de aprendizado de máquina existentes:** Como o RL normalmente usa algoritmos baseados em gradiente para aprender e ajustar funções de política, você vai querer que ele suporte sua biblioteca favorita (Tensorflow, Keras, Pytorch, etc.)
- **Escalabilidade:** RL é computacionalmente intensivo e ter a opção de executar de forma distribuída torna-se importante ao atacar ambientes complexos.
- **Composibilidade:** Os algoritmos de RL normalmente envolvem simulações e muitos outros componentes. Você vai querer uma biblioteca que permita reutilizar componentes de algoritmos de RL, que seja compatível com várias estruturas de aprendizado profundo.

[Aqui](https://docs.google.com/spreadsheets/d/1ZWhViAwCpRqupA5E_xFHSaBaaBZ1wAjO6PvmmEEpXGI/edit#gid=0) você consegue visualizar uma lista com algumas bibliotecas existentes.

<img src="https://i1.wp.com/neptune.ai/wp-content/uploads/RL-tools.png?resize=1024%2C372&ssl=1" width=500>


## Ray RLlib

[Ray](https://docs.ray.io/en/latest/) é uma plataforma de execução distribuída que fornece bases para paralelismo e escalabilidade que são simples de usar e permitem que os programas Python sejam escalados em qualquer lugar, de um notebook a um grande cluster. Além disso, construída sobre o Ray, temos a [RLlib](https://docs.ray.io/en/latest/rllib.html), que fornece uma API unificada que pode ser aproveitada em uma ampla gama de aplicações.

<br>

<img src="https://miro.medium.com/max/1838/1*_bomm09XtiZfQ52Kfz9Ciw.png" width=600>


A RLlib foi projetada para oferecer suporte a várias estruturas de aprendizado profundo (TensorFlow e PyTorch) e pode ser acessada por meio de uma API Python simples. Atualmente, ela vem com uma [série de algoritmos RL](https://docs.ray.io/en/latest/rllib-algorithms.html#available-algorithms-overview).

Em particular, a RLlib permite um desenvolvimento rápido porque torna mais fácil construir algoritmos RL escaláveis ​​por meio da reutilização e montagem de implementações existentes. A RLlib também permite que os desenvolvedores usem redes neurais criadas com várias estruturas de aprendizado profundo e se integra facilmente a simuladores de terceiros.


## Configuração

Você precisará fazer uma cópia deste notebook em seu Google Drive antes de editar. Você pode fazer isso com **Arquivo → Salvar uma cópia no Drive**.

Ambiente da competição
!pip install --upgrade ceia-soccer-twos > /dev/null 2>&1
a versão do ray compatível com a implementação dos agentes disponibilizada é a 1.4.0
!pip install 'aioredis==1.3.1' > /dev/null 2>&1 
!pip install 'aiohttp==3.7.4' > /dev/null 2>&1 
!pip install 'ray==1.4.0' > /dev/null 2>&1 
!pip install 'ray[rllib]==1.4.0' > /dev/null 2>&1 
!pip install 'ray[tune]==1.4.0' > /dev/null 2>&1 
!pip install torch > /dev/null 2>&1 
!pip install lz4 > /dev/null 2>&1 

Dependências necessárias para gravar os vídeos
!apt-get install -y xvfb x11-utils > /dev/null 2>&1 
!pip install pyvirtualdisplay==0.2.* > /dev/null 2>&1 

! wget http://www.atarimania.com/roms/Roms.rar
! mkdir /content/ROM/
! unrar e /content/Roms.rar /content/ROM/ -y
! python -m atari_py.import_roms /content/ROM/ > /dev/null 2>&1

Inicializa uma instância de um display virtual
from pyvirtualdisplay import Display
display = Display(visible=False, size=(1400, 900))
_ = display.start()

In [ ]:
# Carrega a extensão do notebook TensorBoard
%load_ext tensorboard

Como tarefa bônus, experimente com os algoritmos aprendidos no ambiente `soccer_twos`, que será utilizado na competição final deste curso*. Para facilitar, utilize a variação `team_vs_policy` como no laboratório anterior.

<img src="https://raw.githubusercontent.com/bryanoliveira/soccer-twos-env/master/images/screenshot.png" height="400">

> Visualização do ambiente

Este ambiente consiste em um jogo de futebol de carros 2x2, ou seja, o objetivo é marcar um gol no adversário o mais rápido possível. Na variação `team_vs_policy`, seu agente controla um jogador do time azul e joga contra um time aleatório. Mais informações sobre o ambiente podem ser encontradas [no repositório](https://github.com/bryanoliveira/soccer-twos-env) e [na documentação do Unity ml-agents](https://github.com/Unity-Technologies/ml-agents/blob/main/docs/Learning-Environment-Examples.md#soccer-twos).


**Sua tarefa é treinar um agente com a interface do Ray apresentada, experimentando com diferentes algoritmos e hiperparâmetros.**


<br>

*A variação utilizada na competição será a `multiagent_player`, mas agentes treinados para `team_vs_policy` podem ser facilmente adaptados. Na seção "Exportando seu agente treinado" o agente "MyDqnSoccerAgent" faz exatamente isso.

Utilize o ambiente instanciado abaixo para executar o algoritmo de treinamento. Ao final da execução, a recompensa do seu agente por episódio deve tender a +2.

In [1]:
import gym
from gym.wrappers.monitoring.video_recorder import VideoRecorder
from gym.spaces import Discrete, Box

import ray
import ray.rllib.agents.pg as pg
from ray.tune.logger import pretty_print
from ray import tune
from ray.rllib.env.env_context import EnvContext
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.models.torch.fcnet import FullyConnectedNetwork as TorchFC
from ray.rllib.agents.pg import PGTrainer

import numpy as np
import os
import random

import torch
import torch.nn as nn

lz4 not available, disabling sample compression. This will significantly impact RLlib performance. To install lz4, run `pip install lz4`.


In [2]:
import soccer_twos

# Fecha o ambiente caso tenha sido aberto anteriormente
try: env.close()
except: pass

env = soccer_twos.make(
    variation=soccer_twos.EnvType.team_vs_policy,
    flatten_branched=True, # converte o action_space de MultiDiscrete para Discrete
    single_player=True, # controla um dos jogadores enquanto os outros ficam parados
    opponent_policy=lambda *_: 0,  # faz os oponentes ficarem parados
)

# Obtem tamanhos de estado e ação
state_size = env.observation_space.shape[0]
action_size = env.action_space.n

print("Tamanho do estado: {}, tamanho da ação: {}".format(state_size, action_size))
env.close()

[INFO] Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0


INFO:mlagents_envs.environment:Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0


[INFO] Connected new brain: SoccerTwos?team=1


INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=1


[INFO] Connected new brain: SoccerTwos?team=0


INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=0


Tamanho do estado: 336, tamanho da ação: 27


obs_space, act_space = env.observation_space, env.action_space

In [3]:
ray.shutdown()
ray.init(num_gpus=0, ignore_reinit_error=True, include_dashboard=False, log_to_driver=False)

{'node_ip_address': '192.168.15.7',
 'raylet_ip_address': '192.168.15.7',
 'redis_address': '192.168.15.7:6379',
 'object_store_address': 'tcp://127.0.0.1:65497',
 'raylet_socket_name': 'tcp://127.0.0.1:65522',
 'webui_url': None,
 'session_dir': 'C:\\Users\\User\\AppData\\Local\\Temp\\ray\\session_2021-12-10_01-00-42_704270_21040',
 'metrics_export_port': 65528,
 'node_id': 'b3f8c1496e90eaaf4aa0ba54859d8af5ffa14623714da19bd6cbb04d'}

In [4]:
from ray import tune

def create_rllib_env(env_config: dict = {}):
    # suporte a múltiplas instâncias do ambiente na mesma máquina
    if hasattr(env_config, "worker_index"):
        env_config["worker_id"] = (
            env_config.worker_index * env_config.get("num_envs_per_worker", 1)
            + env_config.vector_index
        )
    return soccer_twos.make(**env_config)

# registra ambiente no Ray
tune.registry.register_env("Soccer", create_rllib_env)

Utilize a configuração abaixo como ponto de partida para seus testes. 

A parte mais imporante é a chave `env_config`, que configura o ambiente para ser compatível com o agente disponibilizado para exportação do seu agente. Neste ponto do curso você já deve conseguir testar as outras variações do ambiente e utilizar as APIs do Ray para treinar um agente próximo (ou melhor) do que o [ceia_baseline_agent](https://drive.google.com/file/d/1WEjr48D7QG9uVy1tf4GJAZTpimHtINzE/view). Exemplos de como utilizar as outras variações podem ser encontrados [aqui](https://github.com/dlb-rl/rl-tournament-starter/). Ao utilizar essas variações, você deve utilizar também outras definições de agente para lidar com os diferentes espaços de observação e ação (que também estão presentes nos exemplos).

In [7]:
NUM_ENVS_PER_WORKER = 6

In [8]:
#single player with opponent
analysis = tune.run(
    "PPO",
    config={
        # system settings
        "num_gpus": 0,
        "num_workers": 6,
        "num_envs_per_worker": NUM_ENVS_PER_WORKER,
        "log_level": "INFO",
        "lr": 0.0003,
        "lambda": 0.95,
        "gamma": 0.99,
        'sgd_minibatch_size': 256,
        #'train_batch_size': 4000,
        'clip_param': 0.2,
        'model': {
          'fcnet_hiddens': [256, 256],
        },
        "framework": "torch",
        # RL setup
        "env": "Soccer",
        "env_config": {
            "num_envs_per_worker": NUM_ENVS_PER_WORKER,
            "variation": soccer_twos.EnvType.team_vs_policy,
            "single_player": True,
            "flatten_branched": True,
            "opponent_policy": lambda *_: 0,
        },
    },
    stop={
        # 10000000 (10M) de steps podem ser necessários para aprender uma política útil
        "timesteps_total": 30000000,
        # você também pode limitar por tempo, de acordo com o tempo limite do colab
        "time_total_s": 68400, # 8h
    },
    checkpoint_freq=100,
    checkpoint_at_end=True,
    local_dir=os.path.join("results"),
    restore="results/PPO/PPO_Soccer_0b316_00000_0_2021-12-09_18-29-08/checkpoint_000995/checkpoint-995",
    
)

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 5704552
  custom_metrics: {}
  date: 2021-12-10_01-02-46
  done: false
  episode_len_mean: 38.8433734939759
  episode_media: {}
  episode_reward_max: 1.979200005531311
  episode_reward_mean: 1.8765180663890149
  episode_reward_min: -2.0
  episodes_this_iter: 166
  episodes_total: 79409
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.2
          cur_lr: 0.0003
          entropy: 1.1327780038118362
          entropy_coeff: 0.0
          kl: 0.035540089826099575
          policy_loss: -0.11349753965623677
          total_loss: -0.07972015027189627
          vf_explained_var: 0.8244315981864929
          vf_loss: 0.02666937484173104
    num_agent_steps_sampled: 5704552
    num_steps_sampled: 5704552
    num_steps_trained: 5704552
  iterations_since_restore: 1
  node_ip: 192.168.

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 5712544
  custom_metrics: {}
  date: 2021-12-10_01-03-33
  done: false
  episode_len_mean: 41.43434343434343
  episode_media: {}
  episode_reward_max: 1.979200005531311
  episode_reward_mean: 1.8978080827780444
  episode_reward_min: -2.0
  episodes_this_iter: 198
  episodes_total: 79607
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.30000000000000004
          cur_lr: 0.0003
          entropy: 1.0784552618861198
          entropy_coeff: 0.0
          kl: 0.032717189751565456
          policy_loss: -0.11729610414477065
          total_loss: -0.08005998679436743
          vf_explained_var: 0.7540672421455383
          vf_loss: 0.027420959377195686
    num_agent_steps_sampled: 5712544
    num_steps_sampled: 5712544
    num_steps_trained: 5712544
  iterations_since_restore: 2
 

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 5720536
  custom_metrics: {}
  date: 2021-12-10_01-04-20
  done: false
  episode_len_mean: 40.69543147208122
  episode_media: {}
  episode_reward_max: 1.979200005531311
  episode_reward_mean: 1.9190395991814317
  episode_reward_min: 1.485200047492981
  episodes_this_iter: 197
  episodes_total: 79804
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.45000000000000007
          cur_lr: 0.0003
          entropy: 1.0706304907798767
          entropy_coeff: 0.0
          kl: 0.027400876686442643
          policy_loss: -0.11490186821902171
          total_loss: -0.07616191413399065
          vf_explained_var: 0.7387990951538086
          vf_loss: 0.026409561280161142
    num_agent_steps_sampled: 5720536
    num_steps_sampled: 5720536
    num_steps_trained: 5720536
  iterations_since

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 5728528
  custom_metrics: {}
  date: 2021-12-10_01-05-06
  done: false
  episode_len_mean: 37.87128712871287
  episode_media: {}
  episode_reward_max: 1.9803999662399292
  episode_reward_mean: 1.9056693032236383
  episode_reward_min: -2.0
  episodes_this_iter: 202
  episodes_total: 80006
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.675
          cur_lr: 0.0003
          entropy: 1.0657974276691675
          entropy_coeff: 0.0
          kl: 0.023062850057613105
          policy_loss: -0.111589036139776
          total_loss: -0.07229731665574946
          vf_explained_var: 0.7792162299156189
          vf_loss: 0.023724297352600843
    num_agent_steps_sampled: 5728528
    num_steps_sampled: 5728528
    num_steps_trained: 5728528
  iterations_since_restore: 4
  node_ip: 192.1

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 5736520
  custom_metrics: {}
  date: 2021-12-10_01-05-52
  done: false
  episode_len_mean: 39.072916666666664
  episode_media: {}
  episode_reward_max: 1.979200005531311
  episode_reward_mean: 1.9023416663209598
  episode_reward_min: -2.0
  episodes_this_iter: 192
  episodes_total: 80198
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.0125000000000002
          cur_lr: 0.0003
          entropy: 1.084486361593008
          entropy_coeff: 0.0
          kl: 0.01771753534558229
          policy_loss: -0.10461393708828837
          total_loss: -0.06618848512880504
          vf_explained_var: 0.8192139863967896
          vf_loss: 0.020486452616751194
    num_agent_steps_sampled: 5736520
    num_steps_sampled: 5736520
    num_steps_trained: 5736520
  iterations_since_restore: 5
  n

...

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 10036216
  custom_metrics: {}
  date: 2021-12-10_07-59-59
  done: false
  episode_len_mean: 33.47345132743363
  episode_media: {}
  episode_reward_max: 1.9780000448226929
  episode_reward_mean: 1.9334460143494394
  episode_reward_min: 1.5884000062942505
  episodes_this_iter: 226
  episodes_total: 199680
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.888154523447156
          entropy_coeff: 0.0
          kl: 0.015282942476915196
          policy_loss: -0.1035775258205831
          total_loss: -0.05752717750146985
          vf_explained_var: 0.7535829544067383
          vf_loss: 0.022839380078949034
    num_agent_steps_sampled: 10036216
    num_steps_sampled: 10036216
    num_steps_trained: 10036216
  iterations_s

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 10044208
  custom_metrics: {}
  date: 2021-12-10_08-00-45
  done: false
  episode_len_mean: 36.769911504424776
  episode_media: {}
  episode_reward_max: 1.9808000326156616
  episode_reward_mean: 1.8751309761958839
  episode_reward_min: -2.0
  episodes_this_iter: 226
  episodes_total: 199906
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.9012438971549273
          entropy_coeff: 0.0
          kl: 0.013195696898037568
          policy_loss: -0.0909116894035833
          total_loss: -0.044680996565148234
          vf_explained_var: 0.8282477855682373
          vf_loss: 0.0261897302698344
    num_agent_steps_sampled: 10044208
    num_steps_sampled: 10044208
    num_steps_trained: 10044208
  iterations_since_restore:

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 10052200
  custom_metrics: {}
  date: 2021-12-10_08-01-31
  done: false
  episode_len_mean: 35.62264150943396
  episode_media: {}
  episode_reward_max: 1.9780000448226929
  episode_reward_mean: 1.9111056631466128
  episode_reward_min: -2.0
  episodes_this_iter: 212
  episodes_total: 200118
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.9232953600585461
          entropy_coeff: 0.0
          kl: 0.013957657298306003
          policy_loss: -0.10291810339549556
          total_loss: -0.05378936740453355
          vf_explained_var: 0.812175989151001
          vf_loss: 0.027930541895329952
    num_agent_steps_sampled: 10052200
    num_steps_sampled: 10052200
    num_steps_trained: 10052200
  iterations_since_restore:

Result for PPO_Soccer_e3a41_00000:
  agent_timesteps_total: 10060192
  custom_metrics: {}
  date: 2021-12-10_08-02-17
  done: true
  episode_len_mean: 34.45410628019324
  episode_media: {}
  episode_reward_max: 1.9808000326156616
  episode_reward_mean: 1.9129178737096741
  episode_reward_min: -2.0
  episodes_this_iter: 207
  episodes_total: 200325
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.9531681295484304
          entropy_coeff: 0.0
          kl: 0.013055990944849327
          policy_loss: -0.09784194140229374
          total_loss: -0.046866806398611516
          vf_explained_var: 0.8305264711380005
          vf_loss: 0.031146350491326302
    num_agent_steps_sampled: 10060192
    num_steps_sampled: 10060192
    num_steps_trained: 10060192
  iterations_since_restore

2021-12-10 08:02:18,766	INFO tune.py:549 -- Total run time: 25234.06 seconds (25232.71 seconds for the tuning loop).


In [9]:
ALGORITHM = "PPO"
TRIAL = analysis.get_best_logdir("episode_reward_mean", "max")
CHECKPOINT = analysis.get_best_checkpoint(
  TRIAL,
  "training_iteration",
  "max",
)
TRIAL, CHECKPOINT

('D:\\CEIA\\game\\results\\PPO\\PPO_Soccer_e3a41_00000_0_2021-12-10_01-01-44',
 'D:\\CEIA\\game\\results\\PPO\\PPO_Soccer_e3a41_00000_0_2021-12-10_01-01-44\\checkpoint_001541\\checkpoint-1541')

In [10]:
NUM_ENVS_PER_WORKER = 5

In [11]:
#single player without opponent
analysis = tune.run(
    "PPO",
    config={
        # system settings
        "num_gpus": 0,
        "num_workers": 5,
        "num_envs_per_worker": NUM_ENVS_PER_WORKER,
        "log_level": "INFO",
        #"lr": ray.tune.uniform(1e-7, 1e-3),
        "lr": 0.0003,
        "lambda": 0.95,
        "gamma": 0.99,
        'sgd_minibatch_size': 256,
        #'train_batch_size': 4000,
        'clip_param': 0.2,
        'model': {
          'fcnet_hiddens': [256, 256],
        },
        "framework": "torch",
        # RL setup
        "env": "Soccer",
        "env_config": {
            "num_envs_per_worker": NUM_ENVS_PER_WORKER,
            "variation": soccer_twos.EnvType.team_vs_policy,
            "single_player": True,
            "flatten_branched": True,
            #"opponent_policy": lambda *_: 0,
        },
    },
    stop={
        # 10000000 (10M) de steps podem ser necessários para aprender uma política útil
        "timesteps_total": 30000000,
        # você também pode limitar por tempo, de acordo com o tempo limite do colab
        "time_total_s": 80000, # 12h
    },
    checkpoint_freq=100,
    checkpoint_at_end=True,
    local_dir=os.path.join("results"),
    restore="results/PPO/PPO_Soccer_e3a41_00000_0_2021-12-10_01-01-44/checkpoint_001541/checkpoint-1541",
)

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 10064192
  custom_metrics: {}
  date: 2021-12-10_08-45-49
  done: false
  episode_len_mean: 31.87378640776699
  episode_media: {}
  episode_reward_max: 1.9775999784469604
  episode_reward_mean: 1.8979184465500916
  episode_reward_min: -2.0
  episodes_this_iter: 103
  episodes_total: 200428
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.2
          cur_lr: 0.0003
          entropy: 0.9302581436932087
          entropy_coeff: 0.0
          kl: 0.03477791871409863
          policy_loss: -0.1054547168314457
          total_loss: -0.05323598859831691
          vf_explained_var: 0.767951250076294
          vf_loss: 0.04526314069516957
    num_agent_steps_sampled: 10064192
    num_steps_sampled: 10064192
    num_steps_trained: 10064192
  iterations_since_restore: 1
  node_ip: 192.

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 10068192
  custom_metrics: {}
  date: 2021-12-10_08-46-14
  done: false
  episode_len_mean: 36.2803738317757
  episode_media: {}
  episode_reward_max: 1.9780000448226929
  episode_reward_mean: 1.8589943970475242
  episode_reward_min: -2.0
  episodes_this_iter: 107
  episodes_total: 200535
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.30000000000000004
          cur_lr: 0.0003
          entropy: 0.9310116656124592
          entropy_coeff: 0.0
          kl: 0.03131414589006454
          policy_loss: -0.10720030451193452
          total_loss: -0.06270697840955108
          vf_explained_var: 0.8202623128890991
          vf_loss: 0.03509908728301525
    num_agent_steps_sampled: 10068192
    num_steps_sampled: 10068192
    num_steps_trained: 10068192
  iterations_since_restore: 

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 10072192
  custom_metrics: {}
  date: 2021-12-10_08-46-39
  done: false
  episode_len_mean: 33.4
  episode_media: {}
  episode_reward_max: 1.9788000583648682
  episode_reward_mean: 1.8596000058310374
  episode_reward_min: -2.0
  episodes_this_iter: 105
  episodes_total: 200640
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.45000000000000007
          cur_lr: 0.0003
          entropy: 0.9483561590313911
          entropy_coeff: 0.0
          kl: 0.027060221997089684
          policy_loss: -0.1038367721484974
          total_loss: -0.06388012482784688
          vf_explained_var: 0.8834971785545349
          vf_loss: 0.027779547846876085
    num_agent_steps_sampled: 10072192
    num_steps_sampled: 10072192
    num_steps_trained: 10072192
  iterations_since_restore: 3
  node_ip

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 10076192
  custom_metrics: {}
  date: 2021-12-10_08-47-03
  done: false
  episode_len_mean: 41.94
  episode_media: {}
  episode_reward_max: 1.9788000583648682
  episode_reward_mean: 1.8488160049915314
  episode_reward_min: -2.0
  episodes_this_iter: 82
  episodes_total: 200722
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 0.675
          cur_lr: 0.0003
          entropy: 1.0806021392345428
          entropy_coeff: 0.0
          kl: 0.02150943223387003
          policy_loss: -0.10874131845775992
          total_loss: -0.03935991827165708
          vf_explained_var: 0.8178671598434448
          vf_loss: 0.05486253183335066
    num_agent_steps_sampled: 10076192
    num_steps_sampled: 10076192
    num_steps_trained: 10076192
  iterations_since_restore: 4
  node_ip: 192.168.15.7


Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 10080192
  custom_metrics: {}
  date: 2021-12-10_08-47-28
  done: false
  episode_len_mean: 43.48
  episode_media: {}
  episode_reward_max: 1.982800006866455
  episode_reward_mean: 1.6831360000371933
  episode_reward_min: -2.0
  episodes_this_iter: 96
  episodes_total: 200818
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.0125000000000002
          cur_lr: 0.0003
          entropy: 1.0274541638791561
          entropy_coeff: 0.0
          kl: 0.01586966816103086
          policy_loss: -0.09714628057554364
          total_loss: -0.03121169182122685
          vf_explained_var: 0.8602923154830933
          vf_loss: 0.049866551999002695
    num_agent_steps_sampled: 10080192
    num_steps_sampled: 10080192
    num_steps_trained: 10080192
  iterations_since_restore: 5
  node_ip: 

...

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 11900192
  custom_metrics: {}
  date: 2021-12-10_11-57-56
  done: false
  episode_len_mean: 32.153153153153156
  episode_media: {}
  episode_reward_max: 1.9819999933242798
  episode_reward_mean: 1.83220180197879
  episode_reward_min: -2.0
  episodes_this_iter: 111
  episodes_total: 248215
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.7803399674594402
          entropy_coeff: 0.0
          kl: 0.013380690128542483
          policy_loss: -0.09171905263792723
          total_loss: -0.027643421082757413
          vf_explained_var: 0.7601189613342285
          vf_loss: 0.04375370766501874
    num_agent_steps_sampled: 11900192
    num_steps_sampled: 11900192
    num_steps_trained: 11900192
  iterations_since_restore:

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 11904192
  custom_metrics: {}
  date: 2021-12-10_11-58-21
  done: false
  episode_len_mean: 43.625
  episode_media: {}
  episode_reward_max: 1.9836000204086304
  episode_reward_mean: 1.8375000030948565
  episode_reward_min: -2.0
  episodes_this_iter: 104
  episodes_total: 248319
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.8873762898147106
          entropy_coeff: 0.0
          kl: 0.012954826350323856
          policy_loss: -0.09336647461168468
          total_loss: -0.008808918704744428
          vf_explained_var: 0.6757285594940186
          vf_loss: 0.06488241394981742
    num_agent_steps_sampled: 11904192
    num_steps_sampled: 11904192
    num_steps_trained: 11904192
  iterations_since_restore: 461
  nod

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 11908192
  custom_metrics: {}
  date: 2021-12-10_11-58-46
  done: false
  episode_len_mean: 37.415841584158414
  episode_media: {}
  episode_reward_max: 1.9811999797821045
  episode_reward_mean: 1.8478297065980365
  episode_reward_min: -2.0
  episodes_this_iter: 101
  episodes_total: 248420
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.8957098796963692
          entropy_coeff: 0.0
          kl: 0.013096757349558175
          policy_loss: -0.09600563207641244
          total_loss: -0.024727920826990157
          vf_explained_var: 0.761868953704834
          vf_loss: 0.05138701177202165
    num_agent_steps_sampled: 11908192
    num_steps_sampled: 11908192
    num_steps_trained: 11908192
  iterations_since_restore

Result for PPO_Soccer_a0663_00000:
  agent_timesteps_total: 11912192
  custom_metrics: {}
  date: 2021-12-10_11-59-12
  done: true
  episode_len_mean: 39.77
  episode_media: {}
  episode_reward_max: 1.9811999797821045
  episode_reward_mean: 1.806968002319336
  episode_reward_min: -2.0
  episodes_this_iter: 99
  episodes_total: 248519
  experiment_id: 680584edd9f34418abf7c9e3e3a03506
  hostname: DESKTOP-DGRCPNR
  info:
    learner:
      default_policy:
        learner_stats:
          allreduce_latency: 0.0
          cur_kl_coeff: 1.5187500000000003
          cur_lr: 0.0003
          entropy: 0.8215372450649738
          entropy_coeff: 0.0
          kl: 0.013463641342241317
          policy_loss: -0.09267504364834167
          total_loss: -0.025239087117370218
          vf_explained_var: 0.7879037857055664
          vf_loss: 0.04698805185034871
    num_agent_steps_sampled: 11912192
    num_steps_sampled: 11912192
    num_steps_trained: 11912192
  iterations_since_restore: 463
  node_ip

2021-12-10 11:59:14,038	INFO tune.py:549 -- Total run time: 11644.85 seconds (11643.48 seconds for the tuning loop).
2021-12-10 12:04:07,236	WARNING worker.py:1114 -- The node with node id: b3f8c1496e90eaaf4aa0ba54859d8af5ffa14623714da19bd6cbb04d and ip: 192.168.15.7 has been marked dead because the detector has missed too many heartbeats from it. This can happen when a raylet crashes unexpectedly or has lagging heartbeats.


In [12]:
ALGORITHM = "PPO"
TRIAL = analysis.get_best_logdir("episode_reward_mean", "max")
CHECKPOINT = analysis.get_best_checkpoint(
  TRIAL,
  "training_iteration",
  "max",
)
TRIAL, CHECKPOINT

('D:\\CEIA\\game\\results\\PPO\\PPO_Soccer_a0663_00000_0_2021-12-10_08-45-09',
 'D:\\CEIA\\game\\results\\PPO\\PPO_Soccer_a0663_00000_0_2021-12-10_08-45-09\\checkpoint_002004\\checkpoint-2004')

2021-12-10 13:11:18,990	WARNING worker.py:1114 -- The node with node id: 3a7799307a9a4bb98259731b3b968fedb6392c99fd17292444996333 and ip: 192.168.15.7 has been marked dead because the detector has missed too many heartbeats from it. This can happen when a raylet crashes unexpectedly or has lagging heartbeats.
2021-12-10 13:11:50,288	WARNING worker.py:1114 -- The node with node id: 7239f313cf68583e258f67fec1e50d85949409860bc89636f48129cb and ip: 192.168.15.7 has been marked dead because the detector has missed too many heartbeats from it. This can happen when a raylet crashes unexpectedly or has lagging heartbeats.
2021-12-10 13:12:20,515	WARNING worker.py:1114 -- The node with node id: 367ba46b000ebc5c5976c326c55a8886a399838b2bef998b4767ddbc and ip: 192.168.15.7 has been marked dead because the detector has missed too many heartbeats from it. This can happen when a raylet crashes unexpectedly or has lagging heartbeats.


In [ ]:
import gym
from ray.rllib import MultiAgentEnv
import soccer_twos


class RLLibWrapper(gym.core.Wrapper, MultiAgentEnv):
    """
    A RLLib wrapper so our env can inherit from MultiAgentEnv.
    """

    pass


def create_rllib_env(env_config: dict = {}):
    """
    Creates a RLLib environment and prepares it to be instantiated by Ray workers.
    Args:
        env_config: configuration for the environment.
            You may specify the following keys:
            - variation: one of soccer_twos.EnvType. Defaults to EnvType.multiagent_player.
            - opponent_policy: a Callable for your agent to train against. Defaults to a random policy.
    """
    if hasattr(env_config, "worker_index"):
        env_config["worker_id"] = (
            env_config.worker_index * env_config.get("num_envs_per_worker", 1)
            + env_config.vector_index
        )
    env = soccer_twos.make(**env_config)
    if "multiagent" in env_config and not env_config["multiagent"]:
        # is multiagent by default, is only disabled if explicitly set to False
        return env
    return RLLibWrapper(env)

In [ ]:
if __name__ == "__main__":
    ray.shutdown()
    ray.init(num_gpus=0, ignore_reinit_error=True, include_dashboard=False, log_to_driver=False)

    tune.registry.register_env("Soccer", create_rllib_env)
    temp_env = create_rllib_env({"variation": soccer_twos.EnvType.multiagent_player, "flatten_branched": True})
    obs_space = temp_env.observation_space
    act_space = temp_env.action_space
    
    temp_env.close()

    analysis = tune.run(
        "PPO",
        name="PPO_selfplay_1",
        config={
            # system settings
            # system settings
            "num_gpus": 0,
            "num_workers": 5,
            "num_envs_per_worker": NUM_ENVS_PER_WORKER,
            "log_level": "INFO",
            #"lr": ray.tune.uniform(1e-7, 1e-3),
            "lr": 0.0003,
            "lambda": 0.95,
            "gamma": 0.99,
            'sgd_minibatch_size': 256,
            #'train_batch_size': 4000,
            'clip_param': 0.2,
            'model': {
              'fcnet_hiddens': [256, 256],
            },
            "framework": "torch",
            # RL setup
            "multiagent": {
                "policies": {
                    "default": (None, obs_space, act_space, {}),
                },
                "policy_mapping_fn": tune.function(lambda _: "default"),
                "policies_to_train": ["default"],
            },
            "env": "Soccer",
            "env_config": {
                "num_envs_per_worker": NUM_ENVS_PER_WORKER,
                "variation": soccer_twos.EnvType.multiagent_player,
                "flatten_branched": True,
            },
        },
        stop={
            "timesteps_total": 15000000,  # 15M
            "time_total_s": 14400, # 4h
        },
        checkpoint_freq=100,
        checkpoint_at_end=True,
        local_dir="./ray_results",
        # restore="./ray_results/PPO_selfplay_1/PPO_Soccer_ID/checkpoint_00X/checkpoint-X",
        restore="results/PPO/PPO_Soccer_0b316_00000_0_2021-12-09_18-29-08/checkpoint_000995/checkpoint-995",
    )

    # Gets best trial based on max accuracy across all training iterations.
    best_trial = analysis.get_best_trial("episode_reward_mean", mode="max")
    print(best_trial)
    # Gets best checkpoint for trial based on accuracy.
    best_checkpoint = analysis.get_best_checkpoint(
        trial=best_trial, metric="episode_reward_mean", mode="max"
    )
    print(best_checkpoint)
    print("Done training")

In [ ]:
print(obs_space, act_space)

## Exportando seu agente treinado

Assim como no Lab 02, você pode exportar seu agente treinado para ser executado como competidor no ambiente da competição ou simplesmente assistí-lo. Para isso, devemos definir uma classe de agente que implemente a interface e trate as observações/ações para o formato da competição. Abaixo, configuramos qual experimento/checkpoint exportar e guardamos a implementação em uma variável para salvá-la em um arquivo posteriormente.

In [ ]:
DRIVE_PATH = "results"
DRIVE_PYTHON_PATH = DRIVE_PATH.replace("\\", "")
if not os.path.exists(DRIVE_PYTHON_PATH):
  %mkdir -p $DRIVE_PATH

In [ ]:
print(os.path.dirname(os.path.abspath('__file__')))

In [ ]:
agent_file = f"""
import pickle
import os

import gym
from gym_unity.envs import ActionFlattener
import ray
from ray import tune
from ray.tune.registry import get_trainable_cls

from soccer_twos import AgentInterface, DummyEnv


ALGORITHM = "{ALGORITHM}"
CHECKPOINT_PATH = os.path.join('results')


class MyRaySoccerAgent(AgentInterface):
    def __init__(self, env: gym.Env):
        super().__init__()
        ray.init(ignore_reinit_error=True)

        self.flattener = ActionFlattener(env.action_space.nvec)

        # Load configuration from checkpoint file.
        config_path = ""
        if CHECKPOINT_PATH:
            config_dir = os.path.dirname(CHECKPOINT_PATH)
            config_path = os.path.join(config_dir, "params.pkl")
            # Try parent directory.
            if not os.path.exists(config_path):
                config_path = os.path.join(config_dir, "../params.pkl")

        # Load the config from pickled.
        if os.path.exists(config_path):
            with open(config_path, "rb") as f:
                config = pickle.load(f)
        else:
            # If no config in given checkpoint -> Error.
            raise ValueError(
                "Could not find params.pkl in either the checkpoint dir or "
                "its parent directory!"
            )

        # no need for parallelism on evaluation
        config["num_workers"] = 0
        config["num_gpus"] = 0

        # create a dummy env since it's required but we only care about the policy
        obs_space = env.observation_space
        act_space = self.flattener.action_space
        tune.registry.register_env(
            "DummyEnv",
            lambda *_: DummyEnv(obs_space, act_space),
        )
        config["env"] = "DummyEnv"

        # create the Trainer from config
        cls = get_trainable_cls(ALGORITHM)
        agent = cls(env=config["env"], config=config)
        # load state from checkpoint
        agent.restore(CHECKPOINT_PATH)
        # get default policy for evaluation
        self.policy = agent.get_policy()

    def act(self, observation):
        actions = {{}}
        for player_id in observation:
            # compute_single_action returns a tuple of (action, action_info, ...)
            # as we only need the action, we discard the other elements
            actions[player_id] = self.flattener.lookup_action(
                self.policy.compute_single_action(observation[player_id])[0]
            )
        return actions
"""

In [ ]:
import os
import shutil

agent_name = "my_ray_soccer_agent"
agent_path = os.path.join('results', agent_name, agent_name)
shutil.rmtree(agent_path)
os.makedirs(agent_path)

# salva a classe do agente
with open(os.path.join('', "agent.py"), "w") as f:
    f.write(agent_file)

# salva um __init__ para criar o módulo Python
with open(os.path.join(agent_path, "__init__.py"), "w") as f:
    f.write("from .agent import MyRaySoccerAgent")

# copia o trial inteiro, incluindo os arquivos de configuração do experimento
shutil.copytree(TRIAL, os.path.join(agent_path, TRIAL.split("results/")[1]))

# empacota tudo num arquivo .zip
shutil.make_archive(os.path.join(DRIVE_PATH, agent_name), "zip", os.path.join(DRIVE_PATH, agent_name))

Após empacotar todos os arquivos necessários para a execução do seu agente, será criado um arquivo `minicurso_rl/lab03/my_ray_soccer_agent.zip` nos arquivos do Colab e na pasta correspondente no Google Drive. Baixe o arquivo e extraia-o para alguma pasta no seu computador. 

Assumindo que o ambiente Python já está configurado (e.g. os pacotes no [requirements.txt](https://github.com/dlb-rl/rl-tournament-starter/blob/main/requirements.txt) estão instalados), rode `python -m soccer_twos.watch -m my_ray_soccer_agent` para assistir seu agente jogando contra si mesmo. 

Você também pode testar dois agentes diferentes jogando um contra o outro. Utilize o seguinte comando: `python -m soccer_twos.watch -m1 my_ray_soccer_agent -m2 ceia_baseline_agent`. Você pode baixar o agente *ceia_baseline_agent* [aqui](https://drive.google.com/file/d/1WEjr48D7QG9uVy1tf4GJAZTpimHtINzE/view).